In [29]:
import matplotlib.pyplot as plt 
import matplotlib.image as mpimg
import cv2
import os


%matplotlib inline

### Create training data from images

#### Data: https://www.di.ens.fr/willow/research/seeing3Dchairs/

1. Read data from folders

In [47]:
src_path = "../rendered_chairs"
file_pattern = "{:s}/renders/{:s}"
dst_path = "data/rendered_chairs"

if not os.path.exists(os.path.join(dst_path, "images")):
    os.makedirs(os.path.join(dst_path, "images"))
if not os.path.exists(os.path.join(dst_path, "edges")):
    os.makedirs(os.path.join(dst_path, "edges"))

In [4]:
import scipy.io
mat = scipy.io.loadmat(os.path.join(src_path, 'all_chair_names.mat'))

2. Edge detection. Use detected edges as training data.

In [136]:
%%time

for f in mat['folder_names'][0]:
    for i in mat['instance_names'][0]:
        folder = f[0]
        instance = i[0]
        file = os.path.join(src_path, file_pattern.format(folder, instance))
        img = cv2.imread(file)
        
        
        ## (1) Convert to gray, and threshold
        gray = cv2.cvtColor(img, cv2.COLOR_BGR2GRAY)
        th, threshed = cv2.threshold(gray, 240, 255, cv2.THRESH_BINARY_INV)

        ## (2) Morph-op to remove noise
        kernel = cv2.getStructuringElement(cv2.MORPH_ELLIPSE, (11,11))
        morphed = cv2.morphologyEx(threshed, cv2.MORPH_CLOSE, kernel)

        ## (3) Find the max-area contour
        cnts = cv2.findContours(morphed, cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)[-2]
        cnt = sorted(cnts, key=cv2.contourArea)[-1]

        ## (4) Crop and save it
        x,y,w,h = cv2.boundingRect(cnt)
        dst = img[y:y+h, x:x+w]
        
        ## padding
        height = int( max(0, w - h) / 2.0) + 10
        width = int( max(0, h - w) / 2.0) + 10
        padded = cv2.copyMakeBorder( dst, height, height, width, width, cv2.BORDER_CONSTANT, value = [255, 255, 255])
        
        edges = cv2.bitwise_not(cv2.Canny(padded,0,255))
        
        cv2.imwrite( os.path.join(dst_path, "images/{:s}_{:s}".format(folder, instance)), padded )
        cv2.imwrite( os.path.join(dst_path, "edges/{:s}_{:s}".format(folder, instance)), edges)


CPU times: user 12min 32s, sys: 3min 5s, total: 15min 37s
Wall time: 15h 44min 29s


3. Resize and combine images

In [139]:
!python tools/process.py \
  --input_dir $dst_path/images \
  --operation resize \
  --output_dir $dst_path/resized/images

!python tools/process.py \
  --input_dir $dst_path/edges \
  --operation resize \
  --output_dir $dst_path/resized/edges

!python tools/process.py \
  --input_dir  $dst_path/resized/edges \
  --b_dir $dst_path/resized/images \
  --operation combine \
  --output_dir $dst_path/combined/

/Users/huijie/.pyenv/versions/3.5.7/lib/python3.5/site-packages/tensorflow/python/framework/dtypes.py:516: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/Users/huijie/.pyenv/versions/3.5.7/lib/python3.5/site-packages/tensorflow/python/framework/dtypes.py:517: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/Users/huijie/.pyenv/versions/3.5.7/lib/python3.5/site-packages/tensorflow/python/framework/dtypes.py:518: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/Users/huijie/.pyenv/versions/3.5.7/lib/pyt

39/86366 complete  80.29 images/sec  0m0s elapsed  17m55s remaining
40/86366 complete  80.50 images/sec  0m0s elapsed  17m52s remaining
41/86366 complete  80.70 images/sec  0m0s elapsed  17m49s remaining
42/86366 complete  80.87 images/sec  0m0s elapsed  17m47s remaining
43/86366 complete  81.17 images/sec  0m0s elapsed  17m43s remaining
44/86366 complete  81.24 images/sec  0m0s elapsed  17m42s remaining
45/86366 complete  81.41 images/sec  0m0s elapsed  17m40s remaining
46/86366 complete  81.56 images/sec  0m0s elapsed  17m38s remaining
47/86366 complete  81.83 images/sec  0m0s elapsed  17m34s remaining
48/86366 complete  82.18 images/sec  0m0s elapsed  17m30s remaining
49/86366 complete  82.31 images/sec  0m0s elapsed  17m28s remaining
50/86366 complete  82.37 images/sec  0m0s elapsed  17m27s remaining
51/86366 complete  82.35 images/sec  0m0s elapsed  17m28s remaining
52/86366 complete  82.28 images/sec  0m0s elapsed  17m29s remaining
53/86366 complete  82.31 images/sec  0m0s elapse

162/86366 complete  82.28 images/sec  0m1s elapsed  17m27s remaining
163/86366 complete  82.36 images/sec  0m1s elapsed  17m26s remaining
164/86366 complete  82.47 images/sec  0m1s elapsed  17m25s remaining
165/86366 complete  82.58 images/sec  0m1s elapsed  17m23s remaining
166/86366 complete  82.67 images/sec  0m2s elapsed  17m22s remaining
167/86366 complete  82.75 images/sec  0m2s elapsed  17m21s remaining
168/86366 complete  82.82 images/sec  0m2s elapsed  17m20s remaining
169/86366 complete  82.90 images/sec  0m2s elapsed  17m19s remaining
170/86366 complete  82.96 images/sec  0m2s elapsed  17m18s remaining
171/86366 complete  83.00 images/sec  0m2s elapsed  17m18s remaining
172/86366 complete  83.02 images/sec  0m2s elapsed  17m18s remaining
173/86366 complete  83.01 images/sec  0m2s elapsed  17m18s remaining
174/86366 complete  82.98 images/sec  0m2s elapsed  17m18s remaining
175/86366 complete  82.93 images/sec  0m2s elapsed  17m19s remaining
176/86366 complete  82.84 images/s

282/86366 complete  84.32 images/sec  0m3s elapsed  17m0s remaining
283/86366 complete  84.33 images/sec  0m3s elapsed  17m0s remaining
284/86366 complete  84.37 images/sec  0m3s elapsed  17m0s remaining
285/86366 complete  84.38 images/sec  0m3s elapsed  17m0s remaining
286/86366 complete  84.41 images/sec  0m3s elapsed  16m59s remaining
287/86366 complete  84.44 images/sec  0m3s elapsed  16m59s remaining
288/86366 complete  84.47 images/sec  0m3s elapsed  16m59s remaining
289/86366 complete  84.48 images/sec  0m3s elapsed  16m58s remaining
290/86366 complete  84.51 images/sec  0m3s elapsed  16m58s remaining
291/86366 complete  84.43 images/sec  0m3s elapsed  16m59s remaining
292/86366 complete  84.44 images/sec  0m3s elapsed  16m59s remaining
293/86366 complete  84.44 images/sec  0m3s elapsed  16m59s remaining
294/86366 complete  84.42 images/sec  0m3s elapsed  16m59s remaining
295/86366 complete  84.34 images/sec  0m3s elapsed  17m0s remaining
296/86366 complete  84.30 images/sec  0

405/86366 complete  81.90 images/sec  0m4s elapsed  17m29s remaining
406/86366 complete  81.93 images/sec  0m4s elapsed  17m29s remaining
407/86366 complete  81.95 images/sec  0m4s elapsed  17m28s remaining
408/86366 complete  81.98 images/sec  0m4s elapsed  17m28s remaining
409/86366 complete  82.01 images/sec  0m4s elapsed  17m28s remaining
410/86366 complete  82.05 images/sec  0m4s elapsed  17m27s remaining
411/86366 complete  82.09 images/sec  0m5s elapsed  17m27s remaining
412/86366 complete  82.16 images/sec  0m5s elapsed  17m26s remaining
413/86366 complete  82.20 images/sec  0m5s elapsed  17m25s remaining
414/86366 complete  82.23 images/sec  0m5s elapsed  17m25s remaining
415/86366 complete  82.26 images/sec  0m5s elapsed  17m24s remaining
416/86366 complete  82.28 images/sec  0m5s elapsed  17m24s remaining
417/86366 complete  82.31 images/sec  0m5s elapsed  17m24s remaining
418/86366 complete  82.34 images/sec  0m5s elapsed  17m23s remaining
419/86366 complete  82.36 images/s

...

85812/86366 complete  80.09 images/sec  17m51s elapsed  0m6s remaining
85813/86366 complete  80.09 images/sec  17m51s elapsed  0m6s remaining
85814/86366 complete  80.09 images/sec  17m51s elapsed  0m6s remaining
85815/86366 complete  80.09 images/sec  17m51s elapsed  0m6s remaining
85816/86366 complete  80.09 images/sec  17m51s elapsed  0m6s remaining
85817/86366 complete  80.09 images/sec  17m51s elapsed  0m6s remaining
85818/86366 complete  80.09 images/sec  17m51s elapsed  0m6s remaining
85819/86366 complete  80.09 images/sec  17m51s elapsed  0m6s remaining
85820/86366 complete  80.09 images/sec  17m51s elapsed  0m6s remaining
85821/86366 complete  80.09 images/sec  17m51s elapsed  0m6s remaining
85822/86366 complete  80.09 images/sec  17m51s elapsed  0m6s remaining
85823/86366 complete  80.09 images/sec  17m51s elapsed  0m6s remaining
85824/86366 complete  80.09 images/sec  17m51s elapsed  0m6s remaining
85825/86366 complete  80.09 images/sec  17m51s elapsed  0m6s remaining
85826/

85929/86366 complete  80.08 images/sec  17m53s elapsed  0m5s remaining
85930/86366 complete  80.08 images/sec  17m53s elapsed  0m5s remaining
85931/86366 complete  80.08 images/sec  17m53s elapsed  0m5s remaining
85932/86366 complete  80.08 images/sec  17m53s elapsed  0m5s remaining
85933/86366 complete  80.08 images/sec  17m53s elapsed  0m5s remaining
85934/86366 complete  80.08 images/sec  17m53s elapsed  0m5s remaining
85935/86366 complete  80.08 images/sec  17m53s elapsed  0m5s remaining
85936/86366 complete  80.08 images/sec  17m53s elapsed  0m5s remaining
85937/86366 complete  80.08 images/sec  17m53s elapsed  0m5s remaining
85938/86366 complete  80.07 images/sec  17m53s elapsed  0m5s remaining
85939/86366 complete  80.07 images/sec  17m53s elapsed  0m5s remaining
85940/86366 complete  80.07 images/sec  17m53s elapsed  0m5s remaining
85941/86366 complete  80.07 images/sec  17m53s elapsed  0m5s remaining
85942/86366 complete  80.07 images/sec  17m53s elapsed  0m5s remaining
85943/

86046/86366 complete  80.06 images/sec  17m54s elapsed  0m3s remaining
86047/86366 complete  80.06 images/sec  17m54s elapsed  0m3s remaining
86048/86366 complete  80.06 images/sec  17m54s elapsed  0m3s remaining
86049/86366 complete  80.06 images/sec  17m54s elapsed  0m3s remaining
86050/86366 complete  80.06 images/sec  17m54s elapsed  0m3s remaining
86051/86366 complete  80.06 images/sec  17m54s elapsed  0m3s remaining
86052/86366 complete  80.06 images/sec  17m54s elapsed  0m3s remaining
86053/86366 complete  80.06 images/sec  17m54s elapsed  0m3s remaining
86054/86366 complete  80.06 images/sec  17m54s elapsed  0m3s remaining
86055/86366 complete  80.06 images/sec  17m54s elapsed  0m3s remaining
86056/86366 complete  80.06 images/sec  17m54s elapsed  0m3s remaining
86057/86366 complete  80.06 images/sec  17m54s elapsed  0m3s remaining
86058/86366 complete  80.06 images/sec  17m54s elapsed  0m3s remaining
86059/86366 complete  80.06 images/sec  17m54s elapsed  0m3s remaining
86060/

86163/86366 complete  80.05 images/sec  17m56s elapsed  0m2s remaining
86164/86366 complete  80.05 images/sec  17m56s elapsed  0m2s remaining
86165/86366 complete  80.05 images/sec  17m56s elapsed  0m2s remaining
86166/86366 complete  80.05 images/sec  17m56s elapsed  0m2s remaining
86167/86366 complete  80.05 images/sec  17m56s elapsed  0m2s remaining
86168/86366 complete  80.05 images/sec  17m56s elapsed  0m2s remaining
86169/86366 complete  80.05 images/sec  17m56s elapsed  0m2s remaining
86170/86366 complete  80.05 images/sec  17m56s elapsed  0m2s remaining
86171/86366 complete  80.05 images/sec  17m56s elapsed  0m2s remaining
86172/86366 complete  80.05 images/sec  17m56s elapsed  0m2s remaining
86173/86366 complete  80.05 images/sec  17m56s elapsed  0m2s remaining
86174/86366 complete  80.05 images/sec  17m56s elapsed  0m2s remaining
86175/86366 complete  80.05 images/sec  17m56s elapsed  0m2s remaining
86176/86366 complete  80.05 images/sec  17m56s elapsed  0m2s remaining
86177/

86279/86366 complete  80.04 images/sec  17m57s elapsed  0m1s remaining
86280/86366 complete  80.04 images/sec  17m57s elapsed  0m1s remaining
86281/86366 complete  80.04 images/sec  17m58s elapsed  0m1s remaining
86282/86366 complete  80.04 images/sec  17m58s elapsed  0m1s remaining
86283/86366 complete  80.04 images/sec  17m58s elapsed  0m1s remaining
86284/86366 complete  80.04 images/sec  17m58s elapsed  0m1s remaining
86285/86366 complete  80.04 images/sec  17m58s elapsed  0m1s remaining
86286/86366 complete  80.04 images/sec  17m58s elapsed  0m0s remaining
86287/86366 complete  80.04 images/sec  17m58s elapsed  0m0s remaining
86288/86366 complete  80.04 images/sec  17m58s elapsed  0m0s remaining
86289/86366 complete  80.04 images/sec  17m58s elapsed  0m0s remaining
86290/86366 complete  80.04 images/sec  17m58s elapsed  0m0s remaining
86291/86366 complete  80.04 images/sec  17m58s elapsed  0m0s remaining
86292/86366 complete  80.04 images/sec  17m58s elapsed  0m0s remaining
86293/